
# 连接多种特征提取方法

在许多实际案例中，有多种方法可以从数据集中提取特征。通常，结合几种方法可以获得良好的性能。此示例展示了如何使用 ``FeatureUnion`` 来结合通过PCA和单变量选择获得的特征。

使用此转换器结合特征的好处是，它允许对整个过程进行交叉验证和网格搜索。

在此示例中使用的组合对该数据集并没有特别大的帮助，仅用于说明FeatureUnion的用法。


In [ ]:
# 作者：scikit-learn 开发者
# SPDX-License-Identifier: BSD-3-Clause

from sklearn.datasets import load_iris
from sklearn.decomposition import PCA
from sklearn.feature_selection import SelectKBest
from sklearn.model_selection import GridSearchCV
from sklearn.pipeline import FeatureUnion, Pipeline
from sklearn.svm import SVC

iris = load_iris()

X, y = iris.data, iris.target

# 这个数据集的维度太高了。最好做主成分分析（PCA）：
pca = PCA(n_components=2)

# 也许一些原有的特性也很好？
selection = SelectKBest(k=1)

# 从PCA和单变量选择构建估计器：

combined_features = FeatureUnion([("pca", pca), ("univ_select", selection)])

# 使用组合特征来转换数据集：
X_features = combined_features.fit(X, y).transform(X)
print("Combined space has", X_features.shape[1], "features")

svm = SVC(kernel="linear")

# 对 k、n_components 和 C 进行网格搜索：

pipeline = Pipeline([("features", combined_features), ("svm", svm)])

param_grid = dict(
    features__pca__n_components=[1, 2, 3],
    features__univ_select__k=[1, 2],
    svm__C=[0.1, 1, 10],
)

grid_search = GridSearchCV(pipeline, param_grid=param_grid, verbose=10)
grid_search.fit(X, y)
print(grid_search.best_estimator_)